In [ ]:
#%pip install bertviz
#%pip install ipywidgets

In [2]:
import pandas as pd
import numpy as np
import pickle
import os
from bertviz import model_view, head_view
from transformers import AutoTokenizer, utils, AutoModelForSeq2SeqLM
utils.logging.set_verbosity_error()  # Suppress standard warnings

os.environ["CUDA_VISIBLE_DEVICES"] = "3"


ANALYSIS_POSTFIX = "mined_2024-07-27"

In [3]:
with open(f"../ensemble_learning/reports/results/cd_df_with_s2_{ANALYSIS_POSTFIX}.pickle", "rb") as handle:
    cv_predictions = pickle.load(handle)

with open(f"../ensemble_learning/reports/results/test_results_df_{ANALYSIS_POSTFIX}.pickle", "rb") as handle:
    test_predictions = pickle.load(handle)

with open(f"../ensemble_learning/reports/results/s2_model_results{ANALYSIS_POSTFIX}.pickle", "rb") as handle:
    s2_predictions = pickle.load(handle)

In [4]:
s2_predictions

{'lr': {'rmse': [0.23675730961302235,
   0.20784468101470463,
   0.21343641566375526],
  'mae': [0.1701851842991416, 0.1617669587665141, 0.16621235463884357],
  'rmse_avg': 0.21934613543049408,
  'mae_avg': 0.16605483256816642},
 'svm': {'rmse': [0.16156570072418652, 0.163160244463675, 0.16430359702487446],
  'mae': [0.1294059212854869, 0.13108508553235257, 0.1324083165777544],
  'rmse_avg': 0.16300984740424532,
  'mae_avg': 0.13096644113186462},
 'lgbm': {'rmse': [0.155641620618759,
   0.15710284897663102,
   0.15879273156759988],
  'mae': [0.12495702174995157, 0.12645548309427945, 0.12735950759934206],
  'rmse_avg': 0.15717906705432996,
  'mae_avg': 0.12625733748119103},
 'catboost': {'rmse': [0.153985070002381,
   0.15634868919122072,
   0.15801441111571787],
  'mae': [0.12355906914027556, 0.1260317856981098, 0.1267236126150536],
  'rmse_avg': 0.15611605676977322,
  'mae_avg': 0.125438155817813}}

In [4]:
#model_name = "/home/RDC/zinovyee.hub/H:/zinovyee.hub/IRTG/MLSC/MLSC_DD/ensemble_learning/models/5_epoch_set"  # Find popular HuggingFace models here: https://huggingface.co/models
model_name = "Salesforce/codet5-base-multi-sum"
input_text = "sum(d * 10 ** i for i, d in enumerate(x[::-1]))"  
model = AutoModelForSeq2SeqLM.from_pretrained(model_name, output_attentions=True)  # Configure model to return attention values
tokenizer = AutoTokenizer.from_pretrained(model_name)

# PREPARE AN EXAMPLE
input_ids = tokenizer(input_text, return_tensors="pt").input_ids
generated_ids = model.generate(input_ids, max_length=20)
output_text = tokenizer.decode(generated_ids[0], skip_special_tokens=True)
print(output_text)

encoder_input_ids = tokenizer(input_text, return_tensors="pt", add_special_tokens=True).input_ids
with tokenizer.as_target_tokenizer():
    decoder_input_ids = tokenizer(output_text, return_tensors="pt", add_special_tokens=True).input_ids
outputs = model(input_ids=encoder_input_ids, decoder_input_ids=decoder_input_ids)

encoder_text = tokenizer.convert_ids_to_tokens(encoder_input_ids[0])
decoder_text = tokenizer.convert_ids_to_tokens(decoder_input_ids[0])
print(decoder_text)

/home/RDC/zinovyee.hub/.conda/envs/ensemble/lib/python3.10/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/home/RDC/zinovyee.hub/.conda/envs/ensemble/lib/python3.10/site-packages/transformers/utils/import_utils.py:616: FutureWarning: `torch._dynamo.external_utils.is_compiling` is deprecated. Use `torch.compiler.is_compiling` instead.
  return dynamo.is_compiling()


Sum of the values in the last 10 - bit interval.


/home/RDC/zinovyee.hub/.conda/envs/ensemble/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:3935: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(


['<s>', 'Sum', 'Ġof', 'Ġthe', 'Ġvalues', 'Ġin', 'Ġthe', 'Ġlast', 'Ġ10', 'Ġ-', 'Ġbit', 'Ġinterval', '.', '</s>']


In [15]:
model_view(
    encoder_attention=outputs.encoder_attentions,
    decoder_attention=outputs.decoder_attentions,
    cross_attention=outputs.cross_attentions,
    encoder_tokens= encoder_text,
    decoder_tokens = decoder_text,
    display_mode="light"
)

<IPython.core.display.Javascript object>

In [8]:
from lime import lime_text

from lime.lime_text import LimeTextExplainer
explainer = LimeTextExplainer(class_names=['acceptable', 'non-acceptable'])

In [ ]:
vectorizer = 
model =  

In [ ]:
def lime_classifier(txt):
  txt = fast_encode2(txt, fast_tokenizer, maxlen=400)

  txt = (
      tf.data.Dataset
      .from_tensor_slices(txt)
      .batch(64)
  )
  probs = model.predict(txt)
  pp = 1 - probs
  probs = np.column_stack((pp, probs))
  return probs